# JijModeling 1.12.1 リリースノート

## 機能強化

### Interpreter エラーの可読性向上

[`Interpreter`](https://jij-inc.github.io/JijModeling-Tutorials/apis/jijmodeling.html#Interpreter) で評価エラーが発生した場合、より可読性の高いエラーが表示されるようになりました。例：

In [15]:
import jijmodeling as jm

D = jm.Placeholder("D", dtype=jm.DataType.INTEGER)
T = jm.Placeholder("T", dtype=jm.DataType.INTEGER)
N = jm.Placeholder("N", dtype=jm.DataType.INTEGER)
H = jm.Placeholder("H", shape=(D, T, N))
R = jm.Placeholder("R", shape=(D, N))

x = jm.BinaryVar("x", shape=(D, T, N))
d = jm.Element("d", belong_to=(0, D))
t = jm.Element("t", belong_to=(0, T))
i = jm.Element("i", belong_to=(0, N))

problem = jm.Problem(name="shift_optimization")
problem += jm.Constraint("night_shift", R[d+1, i] <= x[d, T-1, i], forall=[d, i])
problem += jm.sum([d, t, i], x[d, t, i])

problem

In [17]:
num_days = 7
num_times = 3
num_people = 5

data = problem.generate_random_dataset(
    options={
        "D": {"value": num_days},
        "T": {"value": num_times},
        
        "N": {"value": num_people},
    }
)
interp = jm.Interpreter(data)

try:
    interp.eval_problem(problem)
except Exception as e:
    print(e)

Traceback (most recent last):
    while evaluating Problem `shift_optimization',
    while evaluating constraint: `night_shift',
    while evaluating expression `R[d + 1, i] - x[d, T - 1, i]',
    while evaluating expression `R[d + 1, i]',

IndexError: Index [7, 0] is out of range for shape [7, 5]


## バグ修正

### `Interpreter.eval_*` のパフォーマンスバグを修正

以前は、`Interpreter` での式の評価に意図したよりも多くの時間がかかっていました。
これは、OMMX の `Function` に対する演算を繰り返し呼び出していたためで、中間形式との相互変換とメモリの再割り当てが行われていた結果、一部の総和演算で二次関数的にパフォーマンス低下が発生していました。

今リリースから、JijModeling は専用の中間形式を使用するようになり、こうした評価時のオーバーヘッドが大幅に抑えられるようになりました。